## Required Libraries

In [1]:
import os
from os.path import join, isfile
import re
import numpy as np
import sklearn
import tensorflow as tf
import h5py
import time
import scipy.misc
import random
import shutil
import skimage
import skimage.io
import skimage.transform
import warnings
import skipthoughts
warnings.filterwarnings('ignore')
from tensorflow.python.framework import ops

## Creating Dataset

## Generative Adversarial Network Model 

In [16]:
def batch_norm(x,epsilon=1e-5, momentum = 0.9, train = True, name="batch_norm"):
    return tf.contrib.layers.batch_norm(x,
                          decay=momentum, 
                          updates_collections=None,
                          epsilon=epsilon,
                          scale=True,
                          is_training=train,
                          scope=name)

def conv2d(input_, output_dim, k_h=5, k_w=5, d_h=2, d_w=2, stddev=0.02, name='conv2d'):
    with tf.variable_scope(name):
        w = tf.get_variable('w', [k_h, k_w, input_.get_shape()[-1], output_dim],
                            initializer=tf.truncated_normal_initializer(stddev=stddev))
        conv = tf.nn.conv2d(input_, w, strides=[1, d_h, d_w, 1], padding='SAME')
        biases = tf.get_variable('biases', [output_dim], initializer=tf.constant_initializer(0.0))
        conv = tf.reshape(tf.nn.bias_add(conv, biases), conv.get_shape())
        return conv

def deconv2d(input_, output_shape, k_h=5, k_w=5, d_h=2, d_w=2, stddev=0.02,  name="deconv2d", with_w=False):
    with tf.variable_scope(name):
        # filter : [height, width, output_channels, in_channels]
        w = tf.get_variable('w', [k_h, k_w, output_shape[-1], input_.get_shape()[-1]],
              initializer=tf.random_normal_initializer(stddev=stddev))
    
        deconv = tf.nn.conv2d_transpose(input_, w, output_shape=output_shape, strides=[1, d_h, d_w, 1])

        biases = tf.get_variable('biases', [output_shape[-1]], initializer=tf.constant_initializer(0.0))
        deconv = tf.reshape(tf.nn.bias_add(deconv, biases), deconv.get_shape())

        if with_w:
            return deconv, w, biases
        else:
            return deconv

def lrelu(x, leak=0.2):
    return tf.maximum(x, leak*x)

def linear(input_, output_size, stddev=0.02, bias_start=0.0, with_w=False, scope=None):
    shape = input_.get_shape().as_list()
    with tf.variable_scope(scope or "Linear"):
        matrix = tf.get_variable('matrix', [shape[1], output_size], dtype=tf.float32, initializer=tf.random_normal_initializer(stddev=stddev))
        bias = tf.get_variable('bias', [output_size], initializer=tf.constant_initializer(bias_start))
        if with_w:
            return tf.matmul(input_, matrix) + bias, matrix, bias
        else:
            return tf.matmul(input_, matrix) + bias


In [10]:
def generator(options, t_z, t_text_embedding):
    
    s = options['image_size']
    s2, s4, s8, s16 = int(s/2), int(s/4), int(s/8), int(s/16)

    text_embedding = linear(t_text_embedding, options['t_dim'], scope='generator_text_embedding')
    text_embedding = lrelu( text_embedding )

    z_concat = tf.concat(1, [t_z, text_embedding])
    z_ = linear(z_concat, options['gf_dim']*8*s16*s16, scope='generator_linear')
    Layer0 = tf.reshape(z_, [-1, s16, s16, options['gf_dim'] * 8])
    Layer0 = batch_norm(Layer0, name='generator_batchnorm0')
    Layer0 = tf.nn.relu(Layer0)

    Layer1 = deconv2d(Layer0, [options['batch_size'], s8, s8, options['gf_dim']*4], name='generator_Layer1')
    Layer1 = batch_norm(Layer1, name='generator_batchnorm1')
    Layer1 = tf.nn.relu(Layer1)

    Layer2 = deconv2d(Layer1, [options['batch_size'], s4, s4, options['gf_dim']*2], name='generator_Layer2')
    Layer2 = batch_norm(Layer2, name='generator_batchnorm2')
    Layer2 = tf.nn.relu(Layer2)
    
    Layer3 = deconv2d(Layer2, [options['batch_size'], s2, s2, options['gf_dim']*1], name='generator_Layer3')
    Layer3 = batch_norm(Layer3, name='generator_batchnorm3')
    Layer3 = tf.nn.relu(Layer3)

    Layer4 = deconv2d(Layer3, [options['batch_size'], s, s, 3])
    Layer4 = tf.tanh(Layer4)/2. + 0.5
    
    return (Layer4)


In [11]:
def discriminator(options, image, t_text_embedding, reuse=False):
    
    if reuse:
        tf.get_variable_scope().reuse_variables()
        
    Layer0 = conv2d(image, options['df_dim'], name = 'discriminator_Layer0_conv2d')
    Layer0 = lrelu(Layer0)
    
    Layer1 = conv2d(Layer0, options['df_dim']*2, name='discriminator_Layer1_conv2d')
    Layer1 = batch_norm(Layer1, name = 'discriminator_batchnorm1')
    Layer1 = lrelu(Layer1) 
    
    Layer2 = conv2d(Layer1, options['df_dim']*4, name='discriminator_Layer2_conv2d')
    Layer2 = batch_norm(Layer2, name = 'discriminator_batchnorm2')
    Layer2 = lrelu(Layer2) 
    
    Layer3 = conv2d(Layer2, options['df_dim']*8, name='discriminator_Layer3_conv2d')
    Layer3 = batch_norm(Layer3, name = 'discriminator_batchnorm3')
    Layer3 = lrelu(Layer3) 

    # ADD TEXT EMBEDDING TO THE NETWORK
    text_embeddings = linear(t_text_embedding, options['t_dim'], scope='discriminator_text_embedding')
    text_embeddings = lrelu(text_embeddings)
    text_embeddings = tf.expand_dims(text_embeddings,1)
    text_embeddings = tf.expand_dims(text_embeddings,2)
    tiled_embeddings = tf.tile(text_embeddings, [1,4,4,1], name='tiled_embeddings')
    
    Layer3_concat = tf.concat(3, [Layer3, tiled_embeddings],name='Layer3_concat')
    Layer3_concat = conv2d(Layer3_concat, options['df_dim']*8, 1,1,1,1, name = 'discriminator_Layer3_conv2dnew')
    Layer3_concat = batch_norm(Layer3_concat, name='discriminator_batchnorm4')
    Layer3_new = lrelu(Layer3_concat) 

    Layer4a = linear(tf.reshape(Layer3_new, [options['batch_size'], -1]), 1, scope='discriminator_Layer3_linear')
    Layer4 = tf.nn.sigmoid(Layer4a)
    
    return Layer4, Layer4a

## Preparing Data for training 

In [12]:
def load_data():
    print ("Loading Data..............")
    h = h5py.File('flower_tv.hdf5')
    flower_captions = {}
    for item in h.items():
        print (item)
        flower_captions[item[0]] = np.array(item[1])
        image_list = [key for key in flower_captions]
        image_list.sort()

        img = int(len(image_list)*0.75)
        training_image_list = image_list[0:img]
        random.shuffle(training_image_list)

    return {
        'image_list' : training_image_list,
        'captions' : flower_captions,
        'data_length' : len(training_image_list)
    }

def save_for_vis( epoch, batch_no, real_images, generated_images, image_files):
      for i in range(0, real_images.shape[0]):
        fake_image_255 = np.zeros( (256,256,3), dtype=np.uint8)
        fake_images_255 = (generated_images[i,:,:,:])
        scipy.misc.imsave(join('samples/fakeimages/epoch_{}/batch_{}/fake_image_{}.jpg'.format(epoch, batch_no, i)), fake_images_255)
        
def load_image_array(image_file, image_size):
    img = skimage.io.imread(image_file)
    # GRAYSCALE
    if len(img.shape) == 2:
        img_new = np.ndarray( (img.shape[0], img.shape[1], 3), dtype = 'uint8')
        img_new[:,:,0] = img
        img_new[:,:,1] = img
        img_new[:,:,2] = img
        img = img_new
    img_resized = skimage.transform.resize(img, (image_size, image_size))

    # FLIP HORIZONTAL WIRH A PROBABILITY 0.5
    if random.random() > 0.5:
        img_resized = np.fliplr(img_resized)
    
    
    return img_resized.astype('float32')

In [13]:
def get_training_batch(batch_no, batch_size, image_size, z_dim, caption_vector_length, loaded_data = None):
    real_images = np.zeros((batch_size, image_size, image_size, 3))
    wrong_images = np.zeros((batch_size, image_size, image_size, 3))
    captions = np.zeros((batch_size, caption_vector_length))

    cnt = 0
    image_files = []
    for i in range(batch_no * batch_size, batch_no * batch_size + batch_size):
        idx = i % len(loaded_data['image_list'])
        image_file =  join('Data/flowers/jpg/'+loaded_data['image_list'][idx])
        image_array = load_image_array(image_file, image_size)
        real_images[cnt,:,:,:] = image_array

        # Improve this selection of wrong image
        wrong_image_id = random.randint(0,len(loaded_data['image_list'])-1)
        wrong_image_file =  join('Data/flowers/jpg/'+loaded_data['image_list'][wrong_image_id])
        wrong_image_array = load_image_array(wrong_image_file, image_size)
        wrong_images[cnt, :,:,:] = wrong_image_array

        random_caption = random.randint(0,4)
        captions[cnt,:] = loaded_data['captions'][ loaded_data['image_list'][idx] ][ random_caption ][0:caption_vector_length]
        image_files.append( image_file )
        cnt += 1

    z_noise = np.random.uniform(-1, 1, [batch_size, z_dim])
    return real_images, wrong_images, captions, z_noise, image_files

In [39]:
z_dim = 100 # Noise dimension
t_dim = 256 # Text feature dimension
batch_size = 256 # Batch Size
image_size = 64 # Image Size a, a x a (Ch, H * W)
gf_dim = 64 # Number of conv in the first layer gen
df_dim = 64 # Number of conv in the first layer discr
gfc_dim = 1024 # Dimension of gen for fully connected layer 
caption_vector_length = 2400 # Caption Vector Length
learning_rate = 0.0002 # Learning Rate
beta1 = 0.5 # Momentum for Adam Update
epochs = 600 # Max number of epochs

options = {
    'z_dim' : z_dim,
    't_dim' : t_dim,
    'batch_size' : batch_size,
    'image_size' : image_size,
    'gf_dim' : gf_dim,
    'df_dim' : df_dim,
    'gfc_dim' : gfc_dim,
    'caption_vector_length' : caption_vector_length
}

In [42]:
def build_model(options):    
    img_size = options['image_size']
    real_image = tf.placeholder('float32', [options['batch_size'],img_size, img_size, 3 ], name = 'real_image')
    wrong_image = tf.placeholder('float32', [options['batch_size'],img_size, img_size, 3 ], name = 'wrong_image')
    caption = tf.placeholder('float32', [options['batch_size'], options['caption_vector_length']], name = 'real_caption_input')
    z = tf.placeholder('float32', [options['batch_size'], options['z_dim']])

    generated_image = generator(options,z, caption)

    disc_real_image, disc_real_image_logits   = discriminator(options,real_image, caption)
    disc_wrong_image, disc_wrong_image_logits   = discriminator(options,wrong_image, caption, reuse = True)
    disc_fake_image, disc_fake_image_logits   = discriminator(options,generated_image, caption, reuse = True)

    g_loss = tf.reduce_mean(tf.nn.sigmoid_cross_entropy_with_logits(disc_fake_image_logits, tf.ones_like(disc_fake_image)))
    d_loss1 = tf.reduce_mean(tf.nn.sigmoid_cross_entropy_with_logits(disc_real_image_logits, tf.ones_like(disc_real_image)))
    d_loss2 = tf.reduce_mean(tf.nn.sigmoid_cross_entropy_with_logits(disc_wrong_image_logits, tf.zeros_like(disc_wrong_image)))
    d_loss3 = tf.reduce_mean(tf.nn.sigmoid_cross_entropy_with_logits(disc_fake_image_logits, tf.zeros_like(disc_fake_image)))

    d_loss = d_loss1 + d_loss2 + d_loss3

    t_vars = tf.trainable_variables()
    d_vars = [var for var in t_vars if 'discriminator_' in var.name]
    g_vars = [var for var in t_vars if 'generator_' in var.name]

    input_tensors = {
        'real_image' : real_image,
        'wrong_image' : wrong_image,
        'caption' : caption,
        'z' : z
    }

    variables = {
        'd_vars' : d_vars,
        'g_vars' : g_vars
    }

    loss = {
        'g_loss' : g_loss,
        'd_loss' : d_loss
    }

    outputs = {
        'generator' : generated_image
    }

    checks = {
        'd_loss1': d_loss1,
        'd_loss2': d_loss2,
        'd_loss3' : d_loss3,
        'disc_real_image_logits' : disc_real_image_logits,
        'disc_wrong_image_logits' : disc_wrong_image,
        'disc_fake_image_logits' : disc_fake_image_logits
    }
    return input_tensors, variables, loss, outputs, checks

In [18]:
input_tensors, variables, loss, outputs, checks = build_model(options)
d_optim = tf.train.AdamOptimizer(learning_rate, beta1 = beta1).minimize(loss['d_loss'], var_list=variables['d_vars'])
g_optim = tf.train.AdamOptimizer(learning_rate, beta1 = beta1).minimize(loss['g_loss'], var_list=variables['g_vars'])

sess = tf.InteractiveSession()
tf.global_variables_initializer().run()

loaded_data = load_data()

Loading Data..............
('image_00001.jpg', <HDF5 dataset "image_00001.jpg": shape (10, 4800), type "<f4">)
('image_00002.jpg', <HDF5 dataset "image_00002.jpg": shape (10, 4800), type "<f4">)
('image_00003.jpg', <HDF5 dataset "image_00003.jpg": shape (10, 4800), type "<f4">)
('image_00004.jpg', <HDF5 dataset "image_00004.jpg": shape (10, 4800), type "<f4">)
('image_00005.jpg', <HDF5 dataset "image_00005.jpg": shape (10, 4800), type "<f4">)
('image_00006.jpg', <HDF5 dataset "image_00006.jpg": shape (10, 4800), type "<f4">)
('image_00007.jpg', <HDF5 dataset "image_00007.jpg": shape (10, 4800), type "<f4">)
('image_00008.jpg', <HDF5 dataset "image_00008.jpg": shape (10, 4800), type "<f4">)
('image_00009.jpg', <HDF5 dataset "image_00009.jpg": shape (10, 4800), type "<f4">)
('image_00010.jpg', <HDF5 dataset "image_00010.jpg": shape (10, 4800), type "<f4">)
('image_00011.jpg', <HDF5 dataset "image_00011.jpg": shape (10, 4800), type "<f4">)
('image_00012.jpg', <HDF5 dataset "image_00012.jp

('image_00111.jpg', <HDF5 dataset "image_00111.jpg": shape (10, 4800), type "<f4">)
('image_00112.jpg', <HDF5 dataset "image_00112.jpg": shape (10, 4800), type "<f4">)
('image_00113.jpg', <HDF5 dataset "image_00113.jpg": shape (10, 4800), type "<f4">)
('image_00114.jpg', <HDF5 dataset "image_00114.jpg": shape (10, 4800), type "<f4">)
('image_00115.jpg', <HDF5 dataset "image_00115.jpg": shape (10, 4800), type "<f4">)
('image_00116.jpg', <HDF5 dataset "image_00116.jpg": shape (10, 4800), type "<f4">)
('image_00117.jpg', <HDF5 dataset "image_00117.jpg": shape (10, 4800), type "<f4">)
('image_00118.jpg', <HDF5 dataset "image_00118.jpg": shape (10, 4800), type "<f4">)
('image_00119.jpg', <HDF5 dataset "image_00119.jpg": shape (10, 4800), type "<f4">)
('image_00120.jpg', <HDF5 dataset "image_00120.jpg": shape (10, 4800), type "<f4">)
('image_00121.jpg', <HDF5 dataset "image_00121.jpg": shape (10, 4800), type "<f4">)
('image_00122.jpg', <HDF5 dataset "image_00122.jpg": shape (10, 4800), type 

('image_00221.jpg', <HDF5 dataset "image_00221.jpg": shape (10, 4800), type "<f4">)
('image_00222.jpg', <HDF5 dataset "image_00222.jpg": shape (10, 4800), type "<f4">)
('image_00223.jpg', <HDF5 dataset "image_00223.jpg": shape (10, 4800), type "<f4">)
('image_00224.jpg', <HDF5 dataset "image_00224.jpg": shape (10, 4800), type "<f4">)
('image_00225.jpg', <HDF5 dataset "image_00225.jpg": shape (10, 4800), type "<f4">)
('image_00226.jpg', <HDF5 dataset "image_00226.jpg": shape (10, 4800), type "<f4">)
('image_00227.jpg', <HDF5 dataset "image_00227.jpg": shape (10, 4800), type "<f4">)
('image_00228.jpg', <HDF5 dataset "image_00228.jpg": shape (10, 4800), type "<f4">)
('image_00229.jpg', <HDF5 dataset "image_00229.jpg": shape (10, 4800), type "<f4">)
('image_00230.jpg', <HDF5 dataset "image_00230.jpg": shape (10, 4800), type "<f4">)
('image_00231.jpg', <HDF5 dataset "image_00231.jpg": shape (10, 4800), type "<f4">)
('image_00232.jpg', <HDF5 dataset "image_00232.jpg": shape (10, 4800), type 

('image_00326.jpg', <HDF5 dataset "image_00326.jpg": shape (10, 4800), type "<f4">)
('image_00327.jpg', <HDF5 dataset "image_00327.jpg": shape (10, 4800), type "<f4">)
('image_00328.jpg', <HDF5 dataset "image_00328.jpg": shape (10, 4800), type "<f4">)
('image_00329.jpg', <HDF5 dataset "image_00329.jpg": shape (10, 4800), type "<f4">)
('image_00330.jpg', <HDF5 dataset "image_00330.jpg": shape (10, 4800), type "<f4">)
('image_00331.jpg', <HDF5 dataset "image_00331.jpg": shape (10, 4800), type "<f4">)
('image_00332.jpg', <HDF5 dataset "image_00332.jpg": shape (10, 4800), type "<f4">)
('image_00333.jpg', <HDF5 dataset "image_00333.jpg": shape (10, 4800), type "<f4">)
('image_00334.jpg', <HDF5 dataset "image_00334.jpg": shape (10, 4800), type "<f4">)
('image_00335.jpg', <HDF5 dataset "image_00335.jpg": shape (10, 4800), type "<f4">)
('image_00336.jpg', <HDF5 dataset "image_00336.jpg": shape (10, 4800), type "<f4">)
('image_00337.jpg', <HDF5 dataset "image_00337.jpg": shape (10, 4800), type 

('image_00432.jpg', <HDF5 dataset "image_00432.jpg": shape (10, 4800), type "<f4">)
('image_00433.jpg', <HDF5 dataset "image_00433.jpg": shape (10, 4800), type "<f4">)
('image_00434.jpg', <HDF5 dataset "image_00434.jpg": shape (10, 4800), type "<f4">)
('image_00435.jpg', <HDF5 dataset "image_00435.jpg": shape (10, 4800), type "<f4">)
('image_00436.jpg', <HDF5 dataset "image_00436.jpg": shape (10, 4800), type "<f4">)
('image_00437.jpg', <HDF5 dataset "image_00437.jpg": shape (10, 4800), type "<f4">)
('image_00438.jpg', <HDF5 dataset "image_00438.jpg": shape (10, 4800), type "<f4">)
('image_00439.jpg', <HDF5 dataset "image_00439.jpg": shape (10, 4800), type "<f4">)
('image_00440.jpg', <HDF5 dataset "image_00440.jpg": shape (10, 4800), type "<f4">)
('image_00441.jpg', <HDF5 dataset "image_00441.jpg": shape (10, 4800), type "<f4">)
('image_00442.jpg', <HDF5 dataset "image_00442.jpg": shape (10, 4800), type "<f4">)
('image_00443.jpg', <HDF5 dataset "image_00443.jpg": shape (10, 4800), type 

...

('image_07639.jpg', <HDF5 dataset "image_07639.jpg": shape (10, 4800), type "<f4">)
('image_07640.jpg', <HDF5 dataset "image_07640.jpg": shape (10, 4800), type "<f4">)
('image_07641.jpg', <HDF5 dataset "image_07641.jpg": shape (10, 4800), type "<f4">)
('image_07642.jpg', <HDF5 dataset "image_07642.jpg": shape (10, 4800), type "<f4">)
('image_07643.jpg', <HDF5 dataset "image_07643.jpg": shape (10, 4800), type "<f4">)
('image_07644.jpg', <HDF5 dataset "image_07644.jpg": shape (10, 4800), type "<f4">)
('image_07645.jpg', <HDF5 dataset "image_07645.jpg": shape (10, 4800), type "<f4">)
('image_07646.jpg', <HDF5 dataset "image_07646.jpg": shape (10, 4800), type "<f4">)
('image_07647.jpg', <HDF5 dataset "image_07647.jpg": shape (10, 4800), type "<f4">)
('image_07648.jpg', <HDF5 dataset "image_07648.jpg": shape (10, 4800), type "<f4">)
('image_07649.jpg', <HDF5 dataset "image_07649.jpg": shape (10, 4800), type "<f4">)
('image_07650.jpg', <HDF5 dataset "image_07650.jpg": shape (10, 4800), type 

('image_07740.jpg', <HDF5 dataset "image_07740.jpg": shape (10, 4800), type "<f4">)
('image_07741.jpg', <HDF5 dataset "image_07741.jpg": shape (10, 4800), type "<f4">)
('image_07742.jpg', <HDF5 dataset "image_07742.jpg": shape (10, 4800), type "<f4">)
('image_07743.jpg', <HDF5 dataset "image_07743.jpg": shape (10, 4800), type "<f4">)
('image_07744.jpg', <HDF5 dataset "image_07744.jpg": shape (10, 4800), type "<f4">)
('image_07745.jpg', <HDF5 dataset "image_07745.jpg": shape (10, 4800), type "<f4">)
('image_07746.jpg', <HDF5 dataset "image_07746.jpg": shape (10, 4800), type "<f4">)
('image_07747.jpg', <HDF5 dataset "image_07747.jpg": shape (10, 4800), type "<f4">)
('image_07748.jpg', <HDF5 dataset "image_07748.jpg": shape (10, 4800), type "<f4">)
('image_07749.jpg', <HDF5 dataset "image_07749.jpg": shape (10, 4800), type "<f4">)
('image_07750.jpg', <HDF5 dataset "image_07750.jpg": shape (10, 4800), type "<f4">)
('image_07751.jpg', <HDF5 dataset "image_07751.jpg": shape (10, 4800), type 

('image_07945.jpg', <HDF5 dataset "image_07945.jpg": shape (10, 4800), type "<f4">)
('image_07946.jpg', <HDF5 dataset "image_07946.jpg": shape (10, 4800), type "<f4">)
('image_07947.jpg', <HDF5 dataset "image_07947.jpg": shape (10, 4800), type "<f4">)
('image_07948.jpg', <HDF5 dataset "image_07948.jpg": shape (10, 4800), type "<f4">)
('image_07949.jpg', <HDF5 dataset "image_07949.jpg": shape (10, 4800), type "<f4">)
('image_07950.jpg', <HDF5 dataset "image_07950.jpg": shape (10, 4800), type "<f4">)
('image_07951.jpg', <HDF5 dataset "image_07951.jpg": shape (10, 4800), type "<f4">)
('image_07952.jpg', <HDF5 dataset "image_07952.jpg": shape (10, 4800), type "<f4">)
('image_07953.jpg', <HDF5 dataset "image_07953.jpg": shape (10, 4800), type "<f4">)
('image_07954.jpg', <HDF5 dataset "image_07954.jpg": shape (10, 4800), type "<f4">)
('image_07955.jpg', <HDF5 dataset "image_07955.jpg": shape (10, 4800), type "<f4">)
('image_07956.jpg', <HDF5 dataset "image_07956.jpg": shape (10, 4800), type 

('image_08047.jpg', <HDF5 dataset "image_08047.jpg": shape (0, 4800), type "<f4">)
('image_08048.jpg', <HDF5 dataset "image_08048.jpg": shape (10, 4800), type "<f4">)
('image_08049.jpg', <HDF5 dataset "image_08049.jpg": shape (10, 4800), type "<f4">)
('image_08050.jpg', <HDF5 dataset "image_08050.jpg": shape (10, 4800), type "<f4">)
('image_08051.jpg', <HDF5 dataset "image_08051.jpg": shape (10, 4800), type "<f4">)
('image_08052.jpg', <HDF5 dataset "image_08052.jpg": shape (10, 4800), type "<f4">)
('image_08053.jpg', <HDF5 dataset "image_08053.jpg": shape (10, 4800), type "<f4">)
('image_08054.jpg', <HDF5 dataset "image_08054.jpg": shape (10, 4800), type "<f4">)
('image_08055.jpg', <HDF5 dataset "image_08055.jpg": shape (10, 4800), type "<f4">)
('image_08056.jpg', <HDF5 dataset "image_08056.jpg": shape (10, 4800), type "<f4">)
('image_08057.jpg', <HDF5 dataset "image_08057.jpg": shape (10, 4800), type "<f4">)
('image_08058.jpg', <HDF5 dataset "image_08058.jpg": shape (10, 4800), type "

('image_08150.jpg', <HDF5 dataset "image_08150.jpg": shape (10, 4800), type "<f4">)
('image_08151.jpg', <HDF5 dataset "image_08151.jpg": shape (10, 4800), type "<f4">)
('image_08152.jpg', <HDF5 dataset "image_08152.jpg": shape (10, 4800), type "<f4">)
('image_08153.jpg', <HDF5 dataset "image_08153.jpg": shape (10, 4800), type "<f4">)
('image_08154.jpg', <HDF5 dataset "image_08154.jpg": shape (10, 4800), type "<f4">)
('image_08155.jpg', <HDF5 dataset "image_08155.jpg": shape (10, 4800), type "<f4">)
('image_08156.jpg', <HDF5 dataset "image_08156.jpg": shape (10, 4800), type "<f4">)
('image_08157.jpg', <HDF5 dataset "image_08157.jpg": shape (10, 4800), type "<f4">)
('image_08158.jpg', <HDF5 dataset "image_08158.jpg": shape (10, 4800), type "<f4">)
('image_08159.jpg', <HDF5 dataset "image_08159.jpg": shape (10, 4800), type "<f4">)
('image_08160.jpg', <HDF5 dataset "image_08160.jpg": shape (10, 4800), type "<f4">)
('image_08161.jpg', <HDF5 dataset "image_08161.jpg": shape (10, 4800), type 

In [13]:
for i in range(0,epochs+1):
    for j in range(0,24):
        try:
            # os.makedirs('samples/realimages/epoch_{}/batch_{}'.format(i, j))
            os.makedirs('samples/fakeimages/epoch_{}/batch_{}'.format(i, j))
        except:
            pass

In [14]:
import pickle

In [ ]:
losses = {'d_loss' : [], 'g_loss' : []}
saver = tf.train.Saver()
for i in range(epochs):
    batch_no = 0
    while batch_no*batch_size <= loaded_data['data_length']:
        print ("Getting Training Batch")
        real_images, wrong_images, caption_vectors, z_noise, image_files = get_training_batch(batch_no, batch_size, 
            image_size, z_dim, caption_vector_length, loaded_data)

        # DISCR UPDATE
        print ("Discriminator Update")
        check_ts = [ checks['d_loss1'] , checks['d_loss2'], checks['d_loss3']]
        _, d_loss, gen, d1, d2, d3 = sess.run([d_optim, loss['d_loss'], outputs['generator']] + check_ts,
            feed_dict = {
                input_tensors['real_image'] : real_images,
                input_tensors['wrong_image'] : wrong_images,
                input_tensors['caption'] : caption_vectors,
                input_tensors['z'] : z_noise,
            })

        # GEN UPDATE
        print ("Generator Update")
        _, g_loss, gen = sess.run([g_optim, loss['g_loss'], outputs['generator']],
            feed_dict = {
                input_tensors['real_image'] : real_images,
                input_tensors['wrong_image'] : wrong_images,
                input_tensors['caption'] : caption_vectors,
                input_tensors['z'] : z_noise,
            })

        # GEN UPDATE TWICE, to make sure d_loss does not go to 0
        print ("Generator Update second time")
        _, g_loss, gen = sess.run([g_optim, loss['g_loss'], outputs['generator']],
            feed_dict = {
                input_tensors['real_image'] : real_images,
                input_tensors['wrong_image'] : wrong_images,
                input_tensors['caption'] : caption_vectors,
                input_tensors['z'] : z_noise,
            })
        print ("--------Information--------")
        print ("Epoch Number: ", i)
        print ("Batch Nuber: ", batch_no)
        print ("----------LOSSES----------")
        print ("Discriminator Loss: ", d_loss)
        print ("Generator Loss: ", g_loss)        
        losses['d_loss'].append(d_loss)
        losses['g_loss'].append(g_loss)
        print ("Saving Images")
        print ("---------------------------")
        save_for_vis(i,batch_no,real_images, gen, image_files)
        batch_no += 1
    print ("Saving Model")
    print ("-------------------------------")
    pickle.dump( losses, open( "Loss/losses_after_{}_epoch.p".format(i), "wb" ) )
    save_path = saver.save(sess, "Models/model_after_{}_epoch_{}.ckpt".format('flowers', i))

Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  0
Batch Nuber:  0
----------LOSSES----------
Discriminator Loss:  3.0725
Generator Loss:  13.2001
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  0
Batch Nuber:  1
----------LOSSES----------
Discriminator Loss:  7.8829
Generator Loss:  1.99267
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  0
Batch Nuber:  2
----------LOSSES----------
Discriminator Loss:  5.15078
Generator Loss:  9.84125
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  0
Batch Nuber:  3
----------LOSSES----------
Di

Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  1
Batch Nuber:  6
----------LOSSES----------
Discriminator Loss:  2.11569
Generator Loss:  15.3396
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  1
Batch Nuber:  7
----------LOSSES----------
Discriminator Loss:  2.23113
Generator Loss:  14.4563
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  1
Batch Nuber:  8
----------LOSSES----------
Discriminator Loss:  1.49551
Generator Loss:  13.237
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  1
Batch Nuber:  9
----------LOSSES----------
D

Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  2
Batch Nuber:  12
----------LOSSES----------
Discriminator Loss:  1.40228
Generator Loss:  5.00115
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  2
Batch Nuber:  13
----------LOSSES----------
Discriminator Loss:  1.46362
Generator Loss:  4.38879
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  2
Batch Nuber:  14
----------LOSSES----------
Discriminator Loss:  1.27352
Generator Loss:  6.26718
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  2
Batch Nuber:  15
----------LOSSES-------

Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  3
Batch Nuber:  18
----------LOSSES----------
Discriminator Loss:  1.44306
Generator Loss:  5.85404
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  3
Batch Nuber:  19
----------LOSSES----------
Discriminator Loss:  1.57551
Generator Loss:  5.89656
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  3
Batch Nuber:  20
----------LOSSES----------
Discriminator Loss:  1.56557
Generator Loss:  4.08508
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  3
Batch Nuber:  21
----------LOSSES-------

Saving Model
-------------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  5
Batch Nuber:  0
----------LOSSES----------
Discriminator Loss:  1.22659
Generator Loss:  5.3374
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  5
Batch Nuber:  1
----------LOSSES----------
Discriminator Loss:  1.33923
Generator Loss:  6.95055
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  5
Batch Nuber:  2
----------LOSSES----------
Discriminator Loss:  1.37412
Generator Loss:  5.90878
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  5

...

Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  494
Batch Nuber:  8
----------LOSSES----------
Discriminator Loss:  0.196789
Generator Loss:  1.87084
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  494
Batch Nuber:  9
----------LOSSES----------
Discriminator Loss:  0.623499
Generator Loss:  7.78193
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  494
Batch Nuber:  10
----------LOSSES----------
Discriminator Loss:  0.819311
Generator Loss:  2.86197
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  494
Batch Nuber:  11
----------LOSS

Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  495
Batch Nuber:  14
----------LOSSES----------
Discriminator Loss:  0.104816
Generator Loss:  2.46004
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  495
Batch Nuber:  15
----------LOSSES----------
Discriminator Loss:  0.278677
Generator Loss:  3.67193
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  495
Batch Nuber:  16
----------LOSSES----------
Discriminator Loss:  0.17983
Generator Loss:  2.69238
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  495
Batch Nuber:  17
----------LOS

Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  496
Batch Nuber:  20
----------LOSSES----------
Discriminator Loss:  0.306449
Generator Loss:  2.5333
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  496
Batch Nuber:  21
----------LOSSES----------
Discriminator Loss:  0.324342
Generator Loss:  5.79077
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  496
Batch Nuber:  22
----------LOSSES----------
Discriminator Loss:  0.432773
Generator Loss:  3.24831
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  496
Batch Nuber:  23
----------LOS

Generator Update second time
--------Information--------
Epoch Number:  498
Batch Nuber:  1
----------LOSSES----------
Discriminator Loss:  0.461697
Generator Loss:  0.615837
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  498
Batch Nuber:  2
----------LOSSES----------
Discriminator Loss:  0.748974
Generator Loss:  8.18022
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  498
Batch Nuber:  3
----------LOSSES----------
Discriminator Loss:  0.644051
Generator Loss:  4.50979
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  498
Batch Nuber:  4
----------LOSSES----------
Discriminator Loss:  0.0586944
Generator Loss:  2

Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  499
Batch Nuber:  7
----------LOSSES----------
Discriminator Loss:  0.102373
Generator Loss:  4.32293
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  499
Batch Nuber:  8
----------LOSSES----------
Discriminator Loss:  0.156818
Generator Loss:  2.92474
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  499
Batch Nuber:  9
----------LOSSES----------
Discriminator Loss:  0.181628
Generator Loss:  2.89956
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  499
Batch Nuber:  10
----------LOSSE

In [32]:
#saver = tf.train.Saver()
for i in range(500,601):
    batch_no = 0
    while batch_no*batch_size <= loaded_data['data_length']:
        print ("Getting Training Batch")
        real_images, wrong_images, caption_vectors, z_noise, image_files = get_training_batch(batch_no, batch_size, 
            image_size, z_dim, caption_vector_length, loaded_data)

        # DISCR UPDATE
        print ("Discriminator Update")
        check_ts = [ checks['d_loss1'] , checks['d_loss2'], checks['d_loss3']]
        _, d_loss, gen, d1, d2, d3 = sess.run([d_optim, loss['d_loss'], outputs['generator']] + check_ts,
            feed_dict = {
                input_tensors['real_image'] : real_images,
                input_tensors['wrong_image'] : wrong_images,
                input_tensors['caption'] : caption_vectors,
                input_tensors['z'] : z_noise,
            })

        # GEN UPDATE
        print ("Generator Update")
        _, g_loss, gen = sess.run([g_optim, loss['g_loss'], outputs['generator']],
            feed_dict = {
                input_tensors['real_image'] : real_images,
                input_tensors['wrong_image'] : wrong_images,
                input_tensors['caption'] : caption_vectors,
                input_tensors['z'] : z_noise,
            })

        # GEN UPDATE TWICE, to make sure d_loss does not go to 0
        print ("Generator Update second time")
        _, g_loss, gen = sess.run([g_optim, loss['g_loss'], outputs['generator']],
            feed_dict = {
                input_tensors['real_image'] : real_images,
                input_tensors['wrong_image'] : wrong_images,
                input_tensors['caption'] : caption_vectors,
                input_tensors['z'] : z_noise,
            })
        print ("--------Information--------")
        print ("Epoch Number: ", i)
        print ("Batch Nuber: ", batch_no)
        print ("----------LOSSES----------")
        print ("Discriminator Loss: ", d_loss)
        print ("Generator Loss: ", g_loss)        
        losses['d_loss'].append(d_loss)
        losses['g_loss'].append(g_loss)
        print ("Saving Images")
        print ("---------------------------")
        save_for_vis(i,batch_no,real_images, gen, image_files)
        batch_no += 1
    print ("Saving Model")
    print ("-------------------------------")
    pickle.dump( losses, open( "Loss/losses_after_{}_epoch.p".format(i), "wb" ) )
    save_path = saver.save(sess, "Models/model_after_{}_epoch_{}.ckpt".format('flowers', i))

Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  500
Batch Nuber:  0
----------LOSSES----------
Discriminator Loss:  0.200588
Generator Loss:  4.39325
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  500
Batch Nuber:  1
----------LOSSES----------
Discriminator Loss:  0.360276
Generator Loss:  0.749686
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  500
Batch Nuber:  2
----------LOSSES----------
Discriminator Loss:  0.802388
Generator Loss:  10.1406
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  500
Batch Nuber:  3
----------LOSSE

Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  501
Batch Nuber:  6
----------LOSSES----------
Discriminator Loss:  2.40329
Generator Loss:  2.38782
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  501
Batch Nuber:  7
----------LOSSES----------
Discriminator Loss:  0.143287
Generator Loss:  0.874779
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  501
Batch Nuber:  8
----------LOSSES----------
Discriminator Loss:  1.0577
Generator Loss:  9.51267
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  501
Batch Nuber:  9
----------LOSSES--

Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  502
Batch Nuber:  12
----------LOSSES----------
Discriminator Loss:  0.279168
Generator Loss:  0.751243
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  502
Batch Nuber:  13
----------LOSSES----------
Discriminator Loss:  0.644165
Generator Loss:  9.62539
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  502
Batch Nuber:  14
----------LOSSES----------
Discriminator Loss:  1.37407
Generator Loss:  2.26682
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  502
Batch Nuber:  15
----------LO

Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  503
Batch Nuber:  18
----------LOSSES----------
Discriminator Loss:  0.137341
Generator Loss:  1.64255
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  503
Batch Nuber:  19
----------LOSSES----------
Discriminator Loss:  0.263095
Generator Loss:  5.10164
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  503
Batch Nuber:  20
----------LOSSES----------
Discriminator Loss:  0.257216
Generator Loss:  2.37892
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  503
Batch Nuber:  21
----------LO

Saving Model
-------------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  505
Batch Nuber:  0
----------LOSSES----------
Discriminator Loss:  0.328612
Generator Loss:  5.641
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  505
Batch Nuber:  1
----------LOSSES----------
Discriminator Loss:  0.621368
Generator Loss:  0.884774
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  505
Batch Nuber:  2
----------LOSSES----------
Discriminator Loss:  0.42152
Generator Loss:  5.2388
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Num

...

Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  595
Batch Nuber:  11
----------LOSSES----------
Discriminator Loss:  0.0875437
Generator Loss:  2.91021
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  595
Batch Nuber:  12
----------LOSSES----------
Discriminator Loss:  0.190043
Generator Loss:  2.28125
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  595
Batch Nuber:  13
----------LOSSES----------
Discriminator Loss:  0.265858
Generator Loss:  5.6881
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  595
Batch Nuber:  14
----------LO

Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  596
Batch Nuber:  17
----------LOSSES----------
Discriminator Loss:  0.147973
Generator Loss:  4.14726
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  596
Batch Nuber:  18
----------LOSSES----------
Discriminator Loss:  0.0853991
Generator Loss:  3.90681
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  596
Batch Nuber:  19
----------LOSSES----------
Discriminator Loss:  0.252875
Generator Loss:  1.63506
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  596
Batch Nuber:  20
----------L

Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  597
Batch Nuber:  23
----------LOSSES----------
Discriminator Loss:  0.068151
Generator Loss:  1.40444
Saving Images
---------------------------
Saving Model
-------------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  598
Batch Nuber:  0
----------LOSSES----------
Discriminator Loss:  0.758095
Generator Loss:  7.58211
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  598
Batch Nuber:  1
----------LOSSES----------
Discriminator Loss:  0.536572
Generator Loss:  4.24978
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch

Generator Update second time
--------Information--------
Epoch Number:  599
Batch Nuber:  4
----------LOSSES----------
Discriminator Loss:  2.27592
Generator Loss:  12.8892
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  599
Batch Nuber:  5
----------LOSSES----------
Discriminator Loss:  2.87966
Generator Loss:  2.24915
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  599
Batch Nuber:  6
----------LOSSES----------
Discriminator Loss:  0.41741
Generator Loss:  3.4927
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  599
Batch Nuber:  7
----------LOSSES----------
Discriminator Loss:  0.155681
Generator Loss:  4.76655

Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  600
Batch Nuber:  10
----------LOSSES----------
Discriminator Loss:  0.126381
Generator Loss:  3.1826
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  600
Batch Nuber:  11
----------LOSSES----------
Discriminator Loss:  0.161642
Generator Loss:  2.76656
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  600
Batch Nuber:  12
----------LOSSES----------
Discriminator Loss:  0.274485
Generator Loss:  1.66138
Saving Images
---------------------------
Getting Training Batch
Discriminator Update
Generator Update
Generator Update second time
--------Information--------
Epoch Number:  600
Batch Nuber:  13
----------LOS

## Model Testing

In [27]:
#losses1 = pickle.load(open( "Loss/losses_after_499_epoch.p", "rb" ))

In [51]:
def sampler(options, t_z, t_text_embedding):
    
    tf.get_variable_scope().reuse_variables()
    
    s = options['image_size']
    s2, s4, s8, s16 = int(s/2), int(s/4), int(s/8), int(s/16)

    text_embedding = linear(t_text_embedding, options['t_dim'], scope='generator_text_embedding')
    text_embedding = lrelu( text_embedding )

    z_concat = tf.concat(1, [t_z, text_embedding])
    z_ = linear(z_concat, options['gf_dim']*8*s16*s16, scope='generator_linear')
    Layer0 = tf.reshape(z_, [-1, s16, s16, options['gf_dim'] * 8])
    Layer0 = batch_norm(Layer0, train = False, name='generator_batchnorm0')
    Layer0 = tf.nn.relu(Layer0)

    Layer1 = deconv2d(Layer0, [options['batch_size'], s8, s8, options['gf_dim']*4], name='generator_Layer1')
    Layer1 = batch_norm(Layer1, train = False, name='generator_batchnorm1')
    Layer1 = tf.nn.relu(Layer1)

    Layer2 = deconv2d(Layer1, [options['batch_size'], s4, s4, options['gf_dim']*2], name='generator_Layer2')
    Layer2 = batch_norm(Layer2, train = False, name='generator_batchnorm2')
    Layer2 = tf.nn.relu(Layer2)
    
    Layer3 = deconv2d(Layer2, [options['batch_size'], s2, s2, options['gf_dim']*1], name='generator_Layer3')
    Layer3 = batch_norm(Layer3, train = False, name='generator_batchnorm3')
    Layer3 = tf.nn.relu(Layer3)

    Layer4 = deconv2d(Layer3, [options['batch_size'], s, s, 3])
    Layer4 = tf.tanh(Layer4)/2. + 0.5
    
    return (Layer4)


In [52]:
def build_generator(options):
    img_size = options['image_size']
    caption = tf.placeholder('float32', [options['batch_size'], options['caption_vector_length']], name = 'real_caption_input')
    z = tf.placeholder('float32', [options['batch_size'], options['z_dim']])
    fake_image = sampler(options, z, caption)

    input_tensors = {
        'caption' : caption,
        'z_noise' : z
    }

    outputs = {
        'generator' : fake_image
    }
    return input_tensors, outputs

In [53]:
z_dim=100 #Noise Dimension

t_dim=256 #Text feature dimension

image_size=64 #Image Size

gf_dim=64 #Number of conv in the first layer gen.

df_dim=64 #Number of conv in the first layer discr.

gfc_dim=1024 #Dimension of gen untis for for fully connected layer 1024

caption_vector_length=2400 #Caption Vector Length

n_images=5 #Number of Images per Caption


options = {
    'z_dim' : z_dim,
    't_dim' : t_dim,
    'batch_size' : n_images,
    'image_size' : image_size,
    'gf_dim' : gf_dim,
    'df_dim' : df_dim,
    'gfc_dim' : gfc_dim,
    'caption_vector_length' : caption_vector_length
}

In [4]:
with open( 'Test/Test_captions.txt' ) as f:
    captions = f.read().split('\n')

captions = [cap for cap in captions if len(cap) > 0]
print (captions)
model = skipthoughts.load_model()
caption_vectors = skipthoughts.encode(model, captions)

h = h5py.File(join('Test/caption_vectors.hdf5'))
h.create_dataset('vectors', data=caption_vectors)
h.close()

['This flower has petals that are white and has pink shading.', 'This flower has a lot of small purple petals in a dome-like configuration.', 'This flower has long thin yellow petals and alot of yellow anthers in the center.', 'This flower is white yellow in color and has petals that are striped.', 'This flower is white and yellow in color with petals that are wavy and smooth.', 'This flower has upturned petals which are thin and orange with rounded edges.', 'This flower has petals that are dark pink with white edges and pink stamen.']
Loading model parameters...
Compiling encoders...
Loading tables...
Packing up...
16
12
14
15


In [54]:
_, _, _, _, _ = build_model(options)

sess = tf.InteractiveSession()
saver = tf.train.Saver()
saver.restore(sess, 'Models/model_after_flowers_epoch_600.ckpt')

input_tensors, outputs = build_generator(options)

h = h5py.File('Test/caption_vectors.hdf5')
caption_vectors = np.array(h['vectors'])
caption_image_dic = {}
for cn, caption_vector in enumerate(caption_vectors):
    caption_images = []
    noise = np.random.uniform(-1, 1, [n_images, z_dim])
    caption = [ caption_vector[0:options['caption_vector_length']] ] * n_images

    [ gen_image ] = sess.run( [ outputs['generator'] ], 
        feed_dict = {
            input_tensors['caption'] : caption,
            input_tensors['z_noise'] : noise,
        } )

    caption_images = [gen_image[i,:,:,:] for i in range(0, n_images)]
    caption_image_dic[ cn ] = caption_images
    print ("Generated", cn)

for f in os.listdir( join('Test/samples')):
    if os.path.isfile(f):
        os.unlink(join('Test/samples/' + f))

for cn in range(0, len(caption_vectors)):
    caption_images = []
    for i, im in enumerate( caption_image_dic[ cn ] ):
        caption_images.append( im )
        caption_images.append( np.zeros((64, 5, 3)) )
    combined_image = np.concatenate( caption_images[0:-1], axis = 1 )
    scipy.misc.imsave( join('Test/samples/combined_image_{}.jpg'.format(cn)) , combined_image)

Generated 0
Generated 1
Generated 2
Generated 3
Generated 4
Generated 5
Generated 6


In [21]:
import matplotlib.pyplot as plt

def concat_images(imga, imgb):
    """
    Combines two color image ndarrays side-by-side.
    """
    ha,wa = imga.shape[:2]
    hb,wb = imgb.shape[:2]
    max_height = np.max([ha, hb])
    total_width = wa+wb
    new_img = np.zeros(shape=(max_height, total_width, 3), dtype=np.uint8)
    new_img[:ha,:wa]=imga
    new_img[:hb,wa:wa+wb]=imgb
    return new_img

images = ['Test/COM/fake_image_1.jpg', 'Test/COM/fake_image_1a.jpg', 'Test/COM/fake_image_1b.jpg']

def concat_n_images(image_path_list):
    """
    Combines N color images from a list of image paths.
    """
    output = None
    for i, img_path in enumerate(image_path_list):
        img = plt.imread(img_path)[:,:,:3]
        if i==0:
            output = img
        else:
            output = concat_images(output, img)
    return output
output = concat_n_images(images)
from scipy import misc
misc.imsave('Test/COM/00.jpg', output)

In [23]:
import matplotlib.pyplot as plt

def concat_images(imga, imgb):
    """
    Combines two color image ndarrays side-by-side.
    """
    ha,wa = imga.shape[:2]
    hb,wb = imgb.shape[:2]
    max_height = ha + hb
    total_width = np.max([wa,wb])
    new_img = np.zeros(shape=(max_height, total_width, 3), dtype=np.uint8)
    new_img[:ha,:wa]=imga
    new_img[ha:ha+hb,:wb]=imgb
    return new_img

images = ['Test/COM/00.jpg', 'Test/COM/01.jpg', 'Test/COM/02.jpg']

def concat_n_images(image_path_list):
    """
    Combines N color images from a list of image paths.
    """
    output = None
    for i, img_path in enumerate(image_path_list):
        img = plt.imread(img_path)[:,:,:3]
        if i==0:
            output = img
        else:
            output = concat_images(output, img)
    return output
output = concat_n_images(images)
from scipy import misc
misc.imsave('Test/COM/final.jpg', output)